<a href="https://colab.research.google.com/github/Shivang-Quantum/QuantaPytha/blob/Tutort/Deep%20Learning/MovieReviewAnalysis.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import tensorflow as tf

from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences

import tensorflow_datasets as tfds

%matplotlib inline

In [3]:
imdb,info=tfds.load('imdb_reviews',with_info=True,as_supervised=True)

Dl Completed...: 0 url [00:00, ? url/s]

Dl Size...: 0 MiB [00:00, ? MiB/s]

Generating splits...:   0%|          | 0/3 [00:00<?, ? splits/s]

Generating train examples...:   0%|          | 0/25000 [00:00<?, ? examples/s]

Shuffling /root/tensorflow_datasets/imdb_reviews/plain_text/1.0.0.incomplete2QZUT2/imdb_reviews-train.tfrecord…

Generating test examples...:   0%|          | 0/25000 [00:00<?, ? examples/s]

Shuffling /root/tensorflow_datasets/imdb_reviews/plain_text/1.0.0.incomplete2QZUT2/imdb_reviews-test.tfrecord*…

Generating unsupervised examples...:   0%|          | 0/50000 [00:00<?, ? examples/s]

Shuffling /root/tensorflow_datasets/imdb_reviews/plain_text/1.0.0.incomplete2QZUT2/imdb_reviews-unsupervised.t…

Dataset imdb_reviews downloaded and prepared to /root/tensorflow_datasets/imdb_reviews/plain_text/1.0.0. Subsequent calls will reuse this data.


In [4]:
imdb.keys()

dict_keys([Split('train'), Split('test'), Split('unsupervised')])

In [7]:
train_data = imdb['train']
test_data = imdb['test']

print(type(train_data))
print(type(test_data))

<class 'tensorflow.python.data.ops.prefetch_op._PrefetchDataset'>
<class 'tensorflow.python.data.ops.prefetch_op._PrefetchDataset'>


In [8]:
info

tfds.core.DatasetInfo(
    name='imdb_reviews',
    full_name='imdb_reviews/plain_text/1.0.0',
    description="""
    Large Movie Review Dataset. This is a dataset for binary sentiment
    classification containing substantially more data than previous benchmark
    datasets. We provide a set of 25,000 highly polar movie reviews for training,
    and 25,000 for testing. There is additional unlabeled data for use as well.
    """,
    config_description="""
    Plain text
    """,
    homepage='http://ai.stanford.edu/~amaas/data/sentiment/',
    data_dir=PosixGPath('/tmp/tmpi5rbxvo0tfds'),
    file_format=tfrecord,
    download_size=80.23 MiB,
    dataset_size=129.83 MiB,
    features=FeaturesDict({
        'label': ClassLabel(shape=(), dtype=int64, num_classes=2),
        'text': Text(shape=(), dtype=string),
    }),
    supervised_keys=('text', 'label'),
    disable_shuffling=False,
    splits={
        'test': <SplitInfo num_examples=25000, num_shards=1>,
        'train': <SplitInfo

In [10]:
print(len(train_data))
print(len(test_data))

25000
25000


In [13]:
count=1
for data in train_data:
  if count > 5:
    break
  print(type(data))
  review, label=data
  print(review)
  print('\n')
  print(label)
  count+=1

<class 'tuple'>
tf.Tensor(b"This was an absolutely terrible movie. Don't be lured in by Christopher Walken or Michael Ironside. Both are great actors, but this must simply be their worst role in history. Even their great acting could not redeem this movie's ridiculous storyline. This movie is an early nineties US propaganda piece. The most pathetic scenes were those when the Columbian rebels were making their cases for revolutions. Maria Conchita Alonso appeared phony, and her pseudo-love affair with Walken was nothing but a pathetic emotional plug in a movie that was devoid of any real meaning. I am disappointed that there are movies like this, ruining actor's like Christopher Walken's good name. I could barely sit through it.", shape=(), dtype=string)


tf.Tensor(0, shape=(), dtype=int64)
<class 'tuple'>
tf.Tensor(b'I have been known to fall asleep during films, but this is usually due to a combination of things including, really tired, being warm and comfortable on the sette and hav

In [14]:
count=1
for data in test_data:
  if count > 5:
    break
  print(type(data))
  review, label=data
  print(review)
  print('\n')
  print(label)
  count+=1

<class 'tuple'>
tf.Tensor(b"There are films that make careers. For George Romero, it was NIGHT OF THE LIVING DEAD; for Kevin Smith, CLERKS; for Robert Rodriguez, EL MARIACHI. Add to that list Onur Tukel's absolutely amazing DING-A-LING-LESS. Flawless film-making, and as assured and as professional as any of the aforementioned movies. I haven't laughed this hard since I saw THE FULL MONTY. (And, even then, I don't think I laughed quite this hard... So to speak.) Tukel's talent is considerable: DING-A-LING-LESS is so chock full of double entendres that one would have to sit down with a copy of this script and do a line-by-line examination of it to fully appreciate the, uh, breadth and width of it. Every shot is beautifully composed (a clear sign of a sure-handed director), and the performances all around are solid (there's none of the over-the-top scenery chewing one might've expected from a film like this). DING-A-LING-LESS is a film whose time has come.", shape=(), dtype=string)


tf.T

In [15]:
training_sentences = []
training_labels = []

testing_sentences = []
testing_labels = []

In [16]:
for review, label in train_data:
  training_sentences.append(review.numpy().decode('utf8'))
  training_labels.append(label.numpy())

In [17]:
for review, label in test_data:
  testing_sentences.append(review.numpy().decode('utf8'))
  testing_labels.append(label.numpy())

In [18]:
training_sentences[:5]

["This was an absolutely terrible movie. Don't be lured in by Christopher Walken or Michael Ironside. Both are great actors, but this must simply be their worst role in history. Even their great acting could not redeem this movie's ridiculous storyline. This movie is an early nineties US propaganda piece. The most pathetic scenes were those when the Columbian rebels were making their cases for revolutions. Maria Conchita Alonso appeared phony, and her pseudo-love affair with Walken was nothing but a pathetic emotional plug in a movie that was devoid of any real meaning. I am disappointed that there are movies like this, ruining actor's like Christopher Walken's good name. I could barely sit through it.",
 'I have been known to fall asleep during films, but this is usually due to a combination of things including, really tired, being warm and comfortable on the sette and having just eaten a lot. However on this occasion I fell asleep because the film was rubbish. The plot development wa

In [20]:
len(training_sentences)

25000

In [21]:
# tokenizer (only on Training Set)

In [22]:
tokenizer=Tokenizer(oov_token='#OOV',num_words=10000)
tokenizer.fit_on_texts(training_sentences)


In [24]:
# Sequencing

training_sequences=tokenizer.texts_to_sequences(training_sentences)
testing_sequences=tokenizer.texts_to_sequences(testing_sentences)

In [25]:
training_sequences

[[12,
  14,
  33,
  425,
  392,
  18,
  90,
  28,
  1,
  9,
  32,
  1366,
  3585,
  40,
  486,
  1,
  197,
  24,
  85,
  154,
  19,
  12,
  213,
  329,
  28,
  66,
  247,
  215,
  9,
  477,
  58,
  66,
  85,
  114,
  98,
  22,
  5675,
  12,
  1322,
  643,
  767,
  12,
  18,
  7,
  33,
  400,
  8170,
  176,
  2455,
  416,
  2,
  89,
  1231,
  137,
  69,
  146,
  52,
  2,
  1,
  7577,
  69,
  229,
  66,
  2933,
  16,
  1,
  2904,
  1,
  1,
  1479,
  4940,
  3,
  39,
  3900,
  117,
  1584,
  17,
  3585,
  14,
  162,
  19,
  4,
  1231,
  917,
  7917,
  9,
  4,
  18,
  13,
  14,
  4139,
  5,
  99,
  145,
  1214,
  11,
  242,
  683,
  13,
  48,
  24,
  100,
  38,
  12,
  7181,
  5515,
  38,
  1366,
  1,
  50,
  401,
  11,
  98,
  1197,
  867,
  141,
  10],
 [11,
  26,
  75,
  571,
  6,
  805,
  2354,
  313,
  106,
  19,
  12,
  7,
  629,
  686,
  6,
  4,
  2219,
  5,
  181,
  584,
  64,
  1454,
  110,
  2263,
  3,
  3951,
  21,
  2,
  1,
  3,
  258,
  41,
  4677,
  4,
  174,
  188,
  21,
  1

In [28]:
from os import truncate
# Padding
padded_training_seq=pad_sequences(training_sequences,maxlen=150,truncating='post',padding='post')
padded_testing_seq=pad_sequences(testing_sequences,maxlen=150,truncating='post',padding='post')

# Converting Label to ND Array
training_labels=np.array(training_labels)
testing_labels=np.array(testing_labels)



In [34]:
print(padded_training_seq.shape)
print(training_labels.shape)
print(padded_testing_seq.shape)
print(testing_labels.shape)

(25000, 150)
(25000,)
(25000, 150)
(25000,)
